In [1]:
cd ..

/Users/dorislee/Desktop/Research/covid/covid19-vis


In [2]:
import pandas as pd

In [3]:
%load_ext autoreload
%autoreload 2
from chartlib.covid_chart import CovidChart

In [4]:
df = pd.read_csv("data/quarantine-activity-US-Apr16-long.csv", thousands=',')
df2 = pd.read_csv("data/reopening-activity-US-Jun9.csv",index_col=0)
df["Effective Date"] = pd.to_datetime(df["Effective Date"]).dt.strftime("%m-%d-%Y")
df2["Effective Date"] = pd.to_datetime(df2["Effective Date"]).dt.strftime("%m-%d-%Y")
# df2.to_csv("data/reopening-activity-US-Jun9.csv",index=None)
print(len(df))
print(len(df2))

607
108


In [5]:
# Generate state population lookup table
quarantine_df_orig = df[df["Coverage.type"]=="State-wide"]
state_populations = quarantine_df_orig[["State","population_size"]].drop_duplicates()
state_populations = state_populations.rename(columns={'State': 'Province_State'})#,"population_size":"state_population_size"})
state_populations.loc[state_populations["Province_State"]=="Puerto Rico","population_size"] = 3725789 # Obtained from https://www.census.gov/quickfacts/PR
state_populations.to_csv("data/state_population_lookup.csv",index=None)

df2 = df2.rename(columns={'Coverage':'Coverage.type'}) 
df2["Coverage.location"] = df2.State # Coerce all the Coverage location to be State-wide

state_populations.index = state_populations.Province_State
state_populations = state_populations.drop(columns="Province_State",index=None)
state_population_lookup = state_populations.to_dict()
state_population_lookup = state_population_lookup["population_size"]

import json
with open('data/state_population_lookup.json', 'w') as outfile:
    json.dump(state_population_lookup, outfile)

In [7]:
df2["Coverage.type"].unique()

array(['State-wide', 'Selected counties (based on specific metrics)',
       'Selected counties', 'Palm Beach ', 'Miami Dade County',
       'Broward County', 'Lake County', 'Marion County', 'Cass County',
       'Rural areas', 'Selected regions',
       'Selected regions (based on specific metrics)',
       'Selected counties (most of state)'], dtype=object)

In [8]:
df2["Effective Date"].max()

'05-27-2020'

In [9]:
# Change all population size to be the state-wide population, if lower than state, automatically assign as 0.5* state population
def assignPopSize(x):
    stateSize = int(state_population_lookup[x["State"]])
    if (x["Coverage.type"]=='State-wide'):
        return stateSize
    else:
        return round(0.5* stateSize)

In [10]:
df2["population_size"] = df2.apply(assignPopSize, axis=1)
# # df2[df2["Coverage.type"]=='State-wide']
# # df2["population_size"] = df2[df2["Coverage.type"]!='State-wide'].apply(lambda x: 0.5*state_population_lookup[x["State"]],axis=1)

In [12]:
combined_df = pd.concat([df,df2])
print (len(combined_df))

715


In [16]:
combined_df.to_csv("data/combined-activity-US-Jun9-with-partial-pop-b4-Apr16.csv")

#### ---------------------------interventionFootprint.py---------------------------

In [17]:
cd chartlib/

/Users/dorislee/Desktop/Research/covid/covid19-vis/chartlib


In [41]:
# Closure:
# emergency declaration = e/E; restaurant closure = r/R
# border screening = b/B; travel restrictions= t/T; border closures = c/C
# shelter-in-place = l/L; gathering limitations= g/G; k-12 school closures = s/S
# non-essential business closure = n/N
# face covering requirement = f/F

# Opening:
# emergency declaration lifted = a/A; 
# travel restrictions lifted= d/D;
# border closures lifted = k/K;
# shelter-in-place lifted = h/H;
# night-time curfew lifted= i/I; 
# Banning gatherings lifted = j/J;
# Face covering requirement lifted =p/P;
# k-12 school open = m/M;
# Bar and Dine-in Restaurant open = q/Q;
# Non-essential Businesses open = o/O
severityScore = {'e':0.1,'g':0.3, 'c':0.3, 's':0.4,'r':0.6 , 't':0.6, 'n':0.8, 'l':1, 'f':0.5,
                 'a':-0.1, 'd':-0.6, 'k':-0.3, 'h':-1, 'm':-0.8, 'p':-0.5, 'q':-0.6, 'o':-0.8, 'j':-0.3}


import pandas as pd
import numpy as np
from utils import create_lockdown_type, split_into_list, str2emo

quarantine_csv = "../data/combined-activity-US-Jun9-with-partial-pop-b4-Apr16.csv"
quarantine_df = pd.read_csv(quarantine_csv)

quarantine_df = quarantine_df.rename(columns={'Effective.Date' : 'Effective Date', 'State.of.Emergency.Declaration' : 'State of Emergency Declaration', 
                'Travel.Restrictions' : 'Travel Restrictions', 'Shelter.in.place.Order' : 'Shelter-in-place Order', 
                'Gathering.Limitations' : 'Gathering Limitations', 'Banning.Gatherings.of.a.Certain.Size' : 'Banning Gatherings of a Certain Size',
                'K.12.School.Closure' : 'K-12 School Closure', 'Bar.and.Dine.in.Restaurant.Closure' : 'Bar and Dine-in Restaurant Closure',
                'Non.essential.Businesses.Closure' : 'Non-essential Businesses Closure', 'Details..if.any.' : 'Details (if any)',
                'Reference.links' : 'Reference links', 'Face.Covering.Requirements' : 'Face Covering Requirements', 'state_pop_2019' : 'population_size'})
quarantine_df = quarantine_df.drop('Unnamed: 0', axis=1)


groupcol = 'Province_State'

quarantine_df = quarantine_df.rename(columns={'State': 'Province_State', 'Effective Date': 'lockdown_date','Coverage.type':'Coverage'})
quarantine_df = quarantine_df.sort_values('Coverage', ascending=True)
quarantine_df['lockdown_type'] = quarantine_df.apply(lambda x: create_lockdown_type(x, 0), axis=1)
quarantine_df['emoji_string'] = quarantine_df.apply(lambda x: create_lockdown_type(x, 1), axis=1)
quarantine_df['lockdown_type'].replace('', np.nan, inplace=True)

quarantine_df = quarantine_df.dropna(subset=['lockdown_type'])

In [42]:
groupcol = 'Province_State'

quarantine_df = quarantine_df.rename(columns={'State': 'Province_State', 'Effective Date': 'lockdown_date','Coverage.type':'Coverage'})
quarantine_df = quarantine_df.sort_values('Coverage', ascending=True)
quarantine_df['lockdown_type'] = quarantine_df.apply(lambda x: create_lockdown_type(x, 0), axis=1)
quarantine_df['emoji_string'] = quarantine_df.apply(lambda x: create_lockdown_type(x, 1), axis=1)
quarantine_df['lockdown_type'].replace('', np.nan, inplace=True)

quarantine_df = quarantine_df.dropna(subset=['lockdown_type'])

In [43]:
quarantine_df.loc[quarantine_df.lockdown_type=="Regional Border Closure/Visitor Quarantine","emoji_string"]="t"#bugfix
# Breaking up emoji into separate rows for vertical stacking
quarantine_df.emoji_string = quarantine_df.emoji_string.apply(split_into_list)

quarantine_df = quarantine_df.explode(column='emoji_string')
quarantine_df['Coverage'] = quarantine_df.emoji_string.apply(
    lambda x: 'Statewide' if str(x).isupper() else 'Regional'
)
quarantine_df = quarantine_df.sort_values('Coverage', ascending=False)
quarantine_df.emoji_string = quarantine_df.emoji_string.str.lower()
quarantine_df['emoji'] = quarantine_df['emoji_string'].map(str2emo)
quarantine_df['event_index'] = quarantine_df.groupby(['Province_State', 'lockdown_date']).cumcount()


In [44]:
quarantine_cols = ['Province_State', 'Coverage','Coverage.location', 'lockdown_date','population_size','lockdown_type', 'emoji_string', 'emoji',
       'event_index']

print(quarantine_df.columns)
quarantine_df = quarantine_df[quarantine_cols]

# # END modified from _ingest_usa_quarantine_df

quarantine_df_orig = pd.read_csv(quarantine_csv)
quarantine_df_orig = quarantine_df_orig.rename(columns={'Effective.Date' : 'Effective Date', 'State.of.Emergency.Declaration' : 'State of Emergency Declaration', 
                'Travel.Restrictions' : 'Travel Restrictions', 'Shelter.in.place.Order' : 'Shelter-in-place Order', 
                'Gathering.Limitations' : 'Gathering Limitations', 'Banning.Gatherings.of.a.Certain.Size' : 'Banning Gatherings of a Certain Size',
                'K.12.School.Closure' : 'K-12 School Closure', 'Bar.and.Dine.in.Restaurant.Closure' : 'Bar and Dine-in Restaurant Closure',
                'Non.essential.Businesses.Closure' : 'Non-essential Businesses Closure', 'Details..if.any.' : 'Details (if any)',
                'Reference.links' : 'Reference links', 'Face.Covering.Requirements' : 'Face Covering Requirements', 'state_pop_2019' : 'population_size'})
quarantine_df_orig = quarantine_df_orig.drop('Unnamed: 0', axis=1)

# state_populations = quarantine_df_orig[["State","population_size"]].drop_duplicates()
state_populations = state_populations.rename(columns={'State': 'Province_State',"population_size":"state_population_size"})
# state_populations.loc[state_populations["Province_State"]=="Puerto Rico","state_population_size"] = 3725789 # Obtained from https://www.census.gov/quickfacts/PR
# state_populations.state_population_size = state_populations.state_population_size.astype("int")

quarantine_df = quarantine_df.merge(state_populations,on="Province_State")

# # quarantine_df = quarantine_df.dropna(subset=["population_size"])
# quarantine_df.population_size = quarantine_df.population_size.astype("int")

Index(['Province_State', 'Coverage', 'Coverage.location', 'lockdown_date',
       'State of Emergency Declaration', 'Travel Restrictions',
       'Shelter-in-place Order', 'Gathering Limitations',
       'Banning Gatherings of a Certain Size', 'K-12 School Closure',
       'Bar and Dine-in Restaurant Closure',
       'Non-essential Businesses Closure', 'Details (if any)',
       'Reference links', 'Timestamp', 'population_size',
       'population_reference', 'Coverage.county.FIPS', 'Coverage.city.FIPS',
       'population_reference.1', 'Unnamed: 0.1', 'Face Covering Requirements',
       'Details (if any) ', 'lockdown_type', 'emoji_string', 'emoji',
       'event_index'],
      dtype='object')


In [45]:
quarantine_df["severityScore"] = quarantine_df.emoji_string.apply(lambda x: severityScore[x])
quarantine_df.lockdown_date = quarantine_df.lockdown_date.str.replace("/","-")
quarantine_df.lockdown_date = pd.to_datetime(quarantine_df.lockdown_date)
quarantine_df = quarantine_df[['Province_State', 'Coverage', 'Coverage.location', 'lockdown_date',
       'population_size', 'state_population_size', 'severityScore']]

In [83]:
def compute_state_replacements(qdf,state):
    df_state_replacements = []
    qdf = quarantine_df[quarantine_df["Province_State"]==state]
    statewideEvents = qdf[qdf["Coverage"]=="Statewide"]
    relevantCountiesInState= list(set(qdf[qdf["Province_State"]==state]["Coverage.location"]) - set([state]))
    # adding "Others" dummy state populated with statewide population - sum(relevant counties population)
    relevantCountiesInState= list(set(qdf[qdf["Province_State"]==state]["Coverage.location"]) - set([state]))
    relevant_county_population_lookup = qdf[qdf["Coverage.location"].isin(relevantCountiesInState)][["Coverage.location","population_size"]].drop_duplicates()
#     state_population_size = state_populations[state_populations["Province_State"]==state].state_population_size.values[0]
    state_population_size = state_population_lookup[state]
    other_population = state_population_size - relevant_county_population_lookup.population_size.sum()
    qdf.loc[len(qdf)] = [state,"Regional","Others",np.nan,other_population,state_population_size,np.nan]
    relevantCountiesInState  = relevantCountiesInState + ["Others"]
    for statewideEvent in statewideEvents.iterrows(): 
    #     statewideLockdown_date = "2020-03-12"
    #     statewideSeverity = "0.1"
        statewideLockdown_date = statewideEvent[1].lockdown_date
        statewideSeverity = statewideEvent[1].severityScore
        for county in relevantCountiesInState: 
            #print(county)
            #display(qdf[qdf["Coverage.location"]==county])
            try:
                # Catch error since some counties don't show up until a later date, ignore these counties 
                clone = np.repeat(qdf[qdf["Coverage.location"]==county].iloc[0],1)
                clone.lockdown_date = statewideLockdown_date
                clone.severityScore = statewideSeverity
                df_state_replacements.append(clone)
            except (IndexError):
                pass

    #df_state_replacements = pd.concat(df_state_replacements)
    df_state_replacements = pd.DataFrame(df_state_replacements,columns=qdf.columns)
    return df_state_replacements 

In [84]:
def compute_state_intervention_footprint_curve(state):
    qdf = quarantine_df[quarantine_df["Province_State"]==state]
    qdf_additional = compute_state_replacements(qdf,state)
    qdf_result = pd.concat([qdf,qdf_additional])
    # For each date, compute a cumulative max, keeping only the entry with the maximum severity score
    qdf_keep_all=[]
    for ldate in qdf.lockdown_date.unique():
        # ldate = "2020-03-13"
        qdf_before = qdf_result[qdf_result["lockdown_date"]<=ldate]
        print ("----------------")
        print (ldate)
        # Compute the max severity for a given location
#         def minMax(x):
#             if (x>0):
#                 return max
#             else:
#                 return min
#         qdf_before["severityMax"] = qdf_before.groupby("Coverage.location")["severityScore"].transform(minMax)

        # BUG: Assume monotonically increasing strictness in severity score,
        # not accounting for negative reopening scores TODO Change this!!!
#         if (any(qdf_before["severityScore"])<0):
#             transform min
#         else: 
#             transform max
        # OLD CODE
        #qdf_before["severityMax"] = qdf_before.groupby("Coverage.location")["severityScore"].transform(max)
        #qdf_keep = qdf_before[qdf_before["severityScore"] == qdf_before["severityMax"]]
        # Replace with compute the "latest" severity score for a given location
        print ("qdf_before:",qdf_before)
        qdf_before["latest_intervention_date"] = qdf_before.groupby("Coverage.location")["lockdown_date"].transform(max)
        qdf_keep = qdf_before[qdf_before["lockdown_date"] == qdf_before["latest_intervention_date"]]
        print ("qdf_keep:",qdf_keep)
#         qdf_keep = qdf_before
        qdf_keep["dateBefore"] = ldate
        qdf_keep = qdf_keep.drop_duplicates(subset="Coverage.location") # applicable only for the last date when severityMax=1 for multiple lockdown_dates, keep just one so that last entry doesn't exceed 1
        qdf_keep_all.append(qdf_keep)
    #     display(qdf_keep)
    qdf_keep_all = pd.concat(qdf_keep_all)
    
    # compute the intervention footprint for the kept df
    qdf_keep_all["pctStateAffected"]= qdf_keep_all["population_size"]/qdf_keep_all["state_population_size"]
    qdf_keep_all["interventionFootprint"] = qdf_keep_all["pctStateAffected"]*qdf_keep_all["severityScore"]
    # Only keeping Regional information since regions should add up to 1, accounted by "Other". So no need for "Statewide".
    qdf_keep_all = qdf_keep_all[qdf_keep_all["Coverage"]=="Regional"]
    print ("qdf_keep_all:",qdf_keep_all)
    # Sum the intervention footprint based on the date we used for the keep max (note this is based on the lockdown date)
    qdf_keep_all_result = qdf_keep_all.groupby("dateBefore").sum().reset_index()
    return qdf_keep_all_result

In [82]:
df_all = []
for state in quarantine_df.Province_State.unique():
    print (state)
    
    statedf = compute_state_intervention_footprint_curve(state)
    statedf["State"]=state
    df_all.append(statedf)

df_all = pd.concat(df_all)

Wyoming
----------------
2020-05-15T00:00:00.000000000
qdf_before:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
0         Wyoming  Statewide           Wyoming    2020-05-15           578759   
1         Wyoming  Statewide           Wyoming    2020-05-08           578759   
2         Wyoming  Statewide           Wyoming    2020-05-08           578759   
3         Wyoming  Statewide           Wyoming    2020-05-15           578759   
4         Wyoming  Statewide           Wyoming    2020-03-15           578759   
5         Wyoming  Statewide           Wyoming    2020-03-13           578759   
6         Wyoming  Statewide           Wyoming    2020-05-01           578759   
7         Wyoming  Statewide           Wyoming    2020-05-01           578759   
8         Wyoming  Statewide           Wyoming    2020-05-01           578759   
9         Wyoming   Regional             Teton    2020-03-28            23464   
10        Wyoming   Regional           Jac

/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g


qdf_keep_all:    Province_State  Coverage Coverage.location lockdown_date  population_size  \
10  New Hampshire  Regional            Others    2020-03-16          1359711   
10  New Hampshire  Regional            Others    2020-03-13          1359711   
10  New Hampshire  Regional            Others    2020-03-27          1359711   
10  New Hampshire  Regional            Others    2020-03-15          1359711   
10  New Hampshire  Regional            Others    2020-05-18          1359711   
10  New Hampshire  Regional            Others    2020-05-11          1359711   
10  New Hampshire  Regional            Others    2020-05-04          1359711   

    state_population_size  severityScore latest_intervention_date dateBefore  \
10                1359711            0.6               2020-03-16 2020-03-16   
10                1359711            0.1               2020-03-13 2020-03-13   
10                1359711            1.0               2020-03-27 2020-03-27   
10                135971

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g


----------------
2020-03-12T00:00:00.000000000
qdf_before:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
51        Montana  Statewide           Montana    2020-03-12          1068778   
8         Montana   Regional            Others    2020-03-12          1068778   

    state_population_size  severityScore  
51                1068778            0.1  
8                 1068778            0.1  
qdf_keep:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
51        Montana  Statewide           Montana    2020-03-12          1068778   
8         Montana   Regional            Others    2020-03-12          1068778   

    state_population_size  severityScore latest_intervention_date  
51                1068778            0.1               2020-03-12  
8                 1068778            0.1               2020-03-12  
----------------
2020-03-16T00:00:00.000000000
qdf_before:    Province_State   Coverage Coverage.location loc

...

qdf_keep:      Province_State   Coverage Coverage.location lockdown_date  \
1004       Arkansas  Statewide          Arkansas    2020-03-11   
1009       Arkansas   Regional             Grant    2020-03-12   
1010       Arkansas   Regional         Jefferson    2020-03-12   
1011       Arkansas   Regional           Pulaski    2020-03-12   
1012       Arkansas   Regional            Saline    2020-03-12   
11         Arkansas   Regional            Others    2020-03-11   

      population_size  state_population_size  severityScore  \
1004          3017804                3017804            0.1   
1009            18265                3017804            0.4   
1010            66824                3017804            0.4   
1011           391911                3017804            0.4   
1012           122437                3017804            0.4   
11            2418367                3017804            0.1   

     latest_intervention_date  
1004               2020-03-11  
1009               20

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stab

Virginia
----------------
2020-03-30T00:00:00.000000000
qdf_before:      Province_State   Coverage Coverage.location lockdown_date  \
1040       Virginia  Statewide          Virginia    2020-03-30   
1041       Virginia  Statewide          Virginia    2020-03-23   
1042       Virginia  Statewide          Virginia    2020-03-17   
1043       Virginia  Statewide          Virginia    2020-03-17   
1044       Virginia  Statewide          Virginia    2020-03-12   
8          Virginia   Regional            Others    2020-03-30   
8          Virginia   Regional            Others    2020-03-23   
8          Virginia   Regional            Others    2020-03-17   
8          Virginia   Regional            Others    2020-03-17   
8          Virginia   Regional            Others    2020-03-12   

      population_size  state_population_size  severityScore  
1040          8535519                8535519            1.0  
1041          8535519                8535519            0.4  
1042          85355

qdf_keep:      Province_State   Coverage Coverage.location lockdown_date  \
1060  West Virginia  Statewide     West Virginia    2020-03-23   
9     West Virginia   Regional            Others    2020-03-23   

      population_size  state_population_size  severityScore  \
1060          1792147                1792147            1.0   
9             1792147                1792147            1.0   

     latest_intervention_date  
1060               2020-03-23  
9                  2020-03-23  
----------------
2020-03-16T00:00:00.000000000
qdf_before:      Province_State   Coverage Coverage.location lockdown_date  \
1059  West Virginia  Statewide     West Virginia    2020-03-14   
1061  West Virginia  Statewide     West Virginia    2020-03-16   
9     West Virginia   Regional            Others    2020-03-14   
9     West Virginia   Regional            Others    2020-03-16   

      population_size  state_population_size  severityScore  
1059          1792147                1792147         

/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g

In [72]:
df_all.to_csv("../data/interventionFootprintByStateReopeningUpdateJun9.csv")

Alternatively, if we keep original code, we compute the max, this is problematic when we start having negative values, since we still keep flat

In [85]:
def compute_state_intervention_footprint_curve(state):
    qdf = quarantine_df[quarantine_df["Province_State"]==state]
    qdf_additional = compute_state_replacements(qdf,state)
    qdf_result = pd.concat([qdf,qdf_additional])
    # For each date, compute a cumulative max, keeping only the entry with the maximum severity score
    qdf_keep_all=[]
    for ldate in qdf.lockdown_date.unique():
        # ldate = "2020-03-13"
        qdf_before = qdf_result[qdf_result["lockdown_date"]<=ldate]
        print ("----------------")
        print (ldate)
        # Compute the max severity for a given location
#         def minMax(x):
#             if (x>0):
#                 return max
#             else:
#                 return min
#         qdf_before["severityMax"] = qdf_before.groupby("Coverage.location")["severityScore"].transform(minMax)

        # BUG: Assume monotonically increasing strictness in severity score,
        # not accounting for negative reopening scores TODO Change this!!!
#         if (any(qdf_before["severityScore"])<0):
#             transform min
#         else: 
#             transform max
        # OLD CODE
        print ("qdf_before:",qdf_before)
        qdf_before["severityMax"] = qdf_before.groupby("Coverage.location")["severityScore"].transform(max)
        qdf_keep = qdf_before[qdf_before["severityScore"] == qdf_before["severityMax"]]
        # Replace with compute the "latest" severity score for a given location
#         qdf_before["latest_intervention_date"] = qdf_before.groupby("Coverage.location")["lockdown_date"].transform(max)
#         qdf_keep = qdf_before[qdf_before["lockdown_date"] == qdf_before["latest_intervention_date"]]
        print ("qdf_keep:",qdf_keep)
#         qdf_keep = qdf_before
        qdf_keep["dateBefore"] = ldate
        qdf_keep = qdf_keep.drop_duplicates(subset="Coverage.location") # applicable only for the last date when severityMax=1 for multiple lockdown_dates, keep just one so that last entry doesn't exceed 1
        qdf_keep_all.append(qdf_keep)
    #     display(qdf_keep)
    qdf_keep_all = pd.concat(qdf_keep_all)
    
    # compute the intervention footprint for the kept df
    qdf_keep_all["pctStateAffected"]= qdf_keep_all["population_size"]/qdf_keep_all["state_population_size"]
    qdf_keep_all["interventionFootprint"] = qdf_keep_all["pctStateAffected"]*qdf_keep_all["severityScore"]
    # Only keeping Regional information since regions should add up to 1, accounted by "Other". So no need for "Statewide".
    qdf_keep_all = qdf_keep_all[qdf_keep_all["Coverage"]=="Regional"]
    print ("qdf_keep_all:",qdf_keep_all)
    # Sum the intervention footprint based on the date we used for the keep max (note this is based on the lockdown date)
    qdf_keep_all_result = qdf_keep_all.groupby("dateBefore").sum().reset_index()
    return qdf_keep_all_result

In [86]:
df_all = []
for state in quarantine_df.Province_State.unique():
    print (state)
    
    statedf = compute_state_intervention_footprint_curve(state)
    statedf["State"]=state
    df_all.append(statedf)

df_all = pd.concat(df_all)
df_all.to_csv("../data/interventionFootprintByStateReopeningUpdateJun9_MAXseverity.csv")

Wyoming
----------------
2020-05-15T00:00:00.000000000
qdf_before:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
0         Wyoming  Statewide           Wyoming    2020-05-15           578759   
1         Wyoming  Statewide           Wyoming    2020-05-08           578759   
2         Wyoming  Statewide           Wyoming    2020-05-08           578759   
3         Wyoming  Statewide           Wyoming    2020-05-15           578759   
4         Wyoming  Statewide           Wyoming    2020-03-15           578759   
5         Wyoming  Statewide           Wyoming    2020-03-13           578759   
6         Wyoming  Statewide           Wyoming    2020-05-01           578759   
7         Wyoming  Statewide           Wyoming    2020-05-01           578759   
8         Wyoming  Statewide           Wyoming    2020-05-01           578759   
9         Wyoming   Regional             Teton    2020-03-28            23464   
10        Wyoming   Regional           Jac

/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g

qdf_keep:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
15  New Hampshire  Statewide     New Hampshire    2020-03-27          1359711   
10  New Hampshire   Regional            Others    2020-03-27          1359711   

    state_population_size  severityScore  severityMax  
15                1359711            1.0          1.0  
10                1359711            1.0          1.0  
qdf_keep_all:    Province_State  Coverage Coverage.location lockdown_date  population_size  \
10  New Hampshire  Regional            Others    2020-03-16          1359711   
10  New Hampshire  Regional            Others    2020-03-13          1359711   
10  New Hampshire  Regional            Others    2020-03-27          1359711   
10  New Hampshire  Regional            Others    2020-03-15          1359711   
10  New Hampshire  Regional            Others    2020-03-27          1359711   
10  New Hampshire  Regional            Others    2020-03-27          1359711   
10  

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g


2020-05-01T00:00:00.000000000
qdf_before:    Province_State   Coverage Coverage.location lockdown_date  population_size  \
38         Nevada  Statewide            Nevada    2020-03-12          3080156   
39         Nevada  Statewide            Nevada    2020-03-15          3080156   
40         Nevada  Statewide            Nevada    2020-03-17          3080156   
41         Nevada  Statewide            Nevada    2020-03-17          3080156   
42         Nevada  Statewide            Nevada    2020-03-24          3080156   
43         Nevada  Statewide            Nevada    2020-03-24          3080156   
44         Nevada  Statewide            Nevada    2020-05-01          3080156   
13         Nevada   Regional            Others    2020-03-12          3080156   
13         Nevada   Regional            Others    2020-03-15          3080156   
13         Nevada   Regional            Others    2020-03-17          3080156   
13         Nevada   Regional            Others    2020-03-17      

...

/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g

----------------
2020-03-25T00:00:00.000000000
qdf_before:      Province_State   Coverage Coverage.location lockdown_date  \
1013        Indiana  Statewide           Indiana    2020-03-25   
1014        Indiana  Statewide           Indiana    2020-03-19   
1015        Indiana  Statewide           Indiana    2020-03-16   
1016        Indiana  Statewide           Indiana    2020-03-06   
21          Indiana   Regional            Others    2020-03-25   
21          Indiana   Regional            Others    2020-03-19   
21          Indiana   Regional            Others    2020-03-16   
21          Indiana   Regional            Others    2020-03-06   

      population_size  state_population_size  severityScore  
1013          6732219                6732219            1.0  
1014          6732219                6732219            0.4  
1015          6732219                6732219            0.6  
1016          6732219                6732219            0.1  
21            6732219               

/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g

qdf_keep_all:   Province_State  Coverage Coverage.location lockdown_date  population_size  \
8       Virginia  Regional            Others    2020-03-30          8535519   
8       Virginia  Regional            Others    2020-03-23          8535519   
8       Virginia  Regional            Others    2020-03-17          8535519   
8       Virginia  Regional            Others    2020-03-12          8535519   
8       Virginia  Regional            Others    2020-03-30          8535519   
8       Virginia  Regional            Others    2020-03-30          8535519   

   state_population_size  severityScore  severityMax dateBefore  \
8                8535519            1.0          1.0 2020-03-30   
8                8535519            0.4          0.4 2020-03-23   
8                8535519            0.3          0.3 2020-03-17   
8                8535519            0.1          0.1 2020-03-12   
8                8535519            1.0          1.0 2020-05-01   
8                8535519      

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

## Visualization

In [73]:
import pandas as pd
df_all = pd.read_csv("../data/interventionFootprintByStateReopeningUpdateJun9.csv",index_col=0)

In [74]:
df_all["dateBefore"]= pd.to_datetime(df_all.dateBefore)

In [76]:
import altair as alt
chart = alt.Chart(df_all).mark_line().encode(
        x = alt.X("dateBefore"),
        y = alt.Y("interventionFootprint",scale=alt.Scale(0,1) ),
        facet=alt.Facet('State:O', columns=4),
    )
chart.properties(width=150,height=100,title="Raw Intervention Footprint Curve").interactive()

alt.Chart(...)

In [88]:
df_all = pd.read_csv("../data/interventionFootprintByStateReopeningUpdateJun9_MAXseverity.csv",index_col=0)
df_all["dateBefore"]= pd.to_datetime(df_all.dateBefore)
import altair as alt
chart = alt.Chart(df_all).mark_line().encode(
        x = alt.X("dateBefore"),
        y = alt.Y("interventionFootprint",scale=alt.Scale(0,1) ),
        facet=alt.Facet('State:O', columns=4),
    )
chart.properties(width=150,height=100,title="Raw Intervention Footprint Curve").interactive()

alt.Chart(...)

Note this also looks different from the original intervention footprint trajectory before June reopening data, perhaps the timesclae is different?

In [61]:
combined_df[combined_df["State"]=="Pennsylvania"].sort_values("Effective Date")

State                                  Coverage.type  \
453  Pennsylvania                                     State-wide   
455  Pennsylvania                                     State-wide   
488  Pennsylvania                                       Regional   
456  Pennsylvania                                       Regional   
468  Pennsylvania                                       Regional   
459  Pennsylvania                                       Regional   
479  Pennsylvania                                       Regional   
464  Pennsylvania                                       Regional   
478  Pennsylvania                                       Regional   
476  Pennsylvania                                       Regional   
469  Pennsylvania                                       Regional   
480  Pennsylvania                                       Regional   
477  Pennsylvania                                       Regional   
481  Pennsylvania                                       Regional   
486  Pennsylvania                                       Regional   
487  Pennsylvania                                       Regional   
485  Pennsylvania                                       Regional   
473  Pennsylvania                                       Regional   
472  Pennsylvania                                       Regional   
458  Pennsylvania                                       Regional   
460  Pennsylvania                                       Regional   
457  Pennsylvania                                       Regional   
484  Pennsylvania                                       Regional   
463  Pennsylvania                                       Regional   
462  Pennsylvania                                       Regional   
467  Pennsylvania                                       Regional   
466  Pennsylvania                                       Regional   
482  Pennsylvania                                       Regional   
483  Pennsylvania                                       Regional   
461  Pennsylvania                                       Regional   
465  Pennsylvania                                       Regional   
475  Pennsylvania                                       Regional   
474  Pennsylvania                                       Regional   
470  Pennsylvania                                       Regional   
471  Pennsylvania                                       Regional   
454  Pennsylvania                                     State-wide   
78   Pennsylvania  Selected counties (based on specific metrics)   
79   Pennsylvania  Selected counties (based on specific metrics)   
80   Pennsylvania  Selected counties (based on specific metrics)   

        Coverage.location Effective Date State of Emergency Declaration  \
453          Pennsylvania     03-13-2020                            NaN   
455          Pennsylvania     03-16-2020                            NaN   
488  City of Philadelphia     03-23-2020                            NaN   
456             Allegheny     03-23-2020                            NaN   
468              Delaware     03-23-2020                            NaN   
459                 Bucks     03-23-2020                            NaN   
479            Montgomery     03-23-2020                            NaN   
464               Chester     03-23-2020                            NaN   
478                Monroe     03-23-2020                            NaN   
476                Lehigh     03-25-2020                            NaN   
469                  Erie     03-25-2020                            NaN   
480           Northampton     03-25-2020                            NaN   
477               Luzerne     03-27-2020                            NaN   
481                  Pike     03-27-2020                            NaN   
486          Westmoreland     03-27-2020                            NaN   
487           York County     03-27-2020                            NaN   
485             

In [62]:
df_all[df_all["State"]=="Pennsylvania"].sort_values("dateBefore")

dateBefore  population_size  state_population_size  severityScore  \
0  2020-03-13         12801989              435267626           13.6   
1  2020-03-16         12801989              435267626           27.2   
2  2020-03-23         12801989              435267626           28.6   
3  2020-03-25         12801989              435267626           29.2   
4  2020-03-27         12801989              435267626           31.0   
5  2020-03-28         12801989              435267626           31.6   
6  2020-03-30         12801989              435267626           32.4   
7  2020-03-31         12801989              435267626           33.8   
8  2020-04-01         12801989              435267626           34.0   
9  2020-05-08         12801989              435267626           34.0   
10 2020-05-15         12801989              435267626           34.0   

    severityMax  pctStateAffected  interventionFootprint         State  
0          13.6               1.0               0.400000  Pennsylvania  
1          27.2               1.0               0.800000  Pennsylvania  
2          28.6               1.0               0.886258  Pennsylvania  
3          29.2               1.0               0.901011  Pennsylvania  
4          31.0               1.0               0.941426  Pennsylvania  
5          31.6               1.0               0.949756  Pennsylvania  
6          32.4               1.0               0.961273  Pennsylvania  
7          33.8               1.0               0.969898  Pennsylvania  
8          34.0               1.0               1.000000  Pennsylvania  
9          34.0               1.0               1.000000  Pennsylvania  
10         34.0               1.0               1.000000  Pennsylvania

In [40]:
combined_df[(combined_df["State"]=="Pennsylvania") &(combined_df["Effective Date"]<"03-16-2020")]

State Coverage.type Coverage.location Effective Date  \
453  Pennsylvania    State-wide      Pennsylvania     03-13-2020   

    State of Emergency Declaration Travel Restrictions Shelter-in-place Order  \
453                            NaN                 NaN                    NaN   

    Gathering Limitations  Banning Gatherings of a Certain Size  \
453                   NaN                                   NaN   

    K-12 School Closure  ...  \
453      Schools closed  ...   

                                       Reference links Timestamp  \
453  https://en.wikipedia.org/wiki/2020_coronavirus...   4/14/20   

    population_size population_reference Coverage.county.FIPS  \
453        12801989                 42.0                  NaN   

     Coverage.city.FIPS                             population_reference.1  \
453                 NaN  https://www.census.gov/data/datasets/time-seri...   

    Unnamed: 0.1  Face Covering Requirements Details (if any)   
453          NaN                         NaN               NaN  

[1 rows x 23 columns]

### Smoothing with step functions

In [77]:
tseries = df_all.pivot(index="State",columns='dateBefore',values="interventionFootprint")
tseries[tseries.columns.min()] = tseries[tseries.columns.min()].fillna(0)
tseries[tseries.columns.max()] = tseries[tseries.columns.max()].fillna(tseries.max(axis=1))
tseries.columns = pd.DatetimeIndex(tseries.columns)
tseries = tseries.interpolate('zero',axis=1)
tseries4plot = tseries.transpose().melt()
series = []
for state in tseries4plot.State.unique():
    series.extend(range(40))
index = pd.Series(series)
tseries4plot["index"]=index

In [78]:
import altair as alt
chart = alt.Chart(tseries4plot).mark_line().encode(
        x = alt.X("index"),
        y = alt.Y("value", scale=alt.Scale(0,1)),
        facet=alt.Facet('State:O', columns=4),
    )
chart.properties(width=150,height=100,title="Step-Function Curve").interactive()

alt.Chart(...)